In [2]:
import sys
sys.path += ['..']

from data_collection.data_collection import LoggerSet, Logger

import numpy as np
import pandas as pd
import plotly.express as px
from data_collection.video_data import get_frame_iterator
from pathlib import Path
from typing import Iterable, Tuple, List
from tqdm import tqdm
import datetime
import tensorflow as tf
import tensorflow.keras as keras

%load_ext autoreload
%autoreload 2


# Note
- Condition: output p instead of angular velocity
- Using sigmoid for the last activation function
- doing much worse - the burstiness was likely the reason for the bad performance

# Loading data 

In [1]:
from with_linear_acc import Session
sessions = Session.load_multiple_session('./data')
frames, df = Session.concatenate_multiple_sessions(sessions)

2024-06-11 19:58:25.367377: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-11 19:58:26.058578: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
[mov,mp4,m4a,3gp,3g2,mj2 @ 0x5b8af1ba36c0] moov atom not found


## Inspection only

In [3]:
df = sessions[0].data['angular_speed_control_df']

In [4]:

def mean_nominmax(x):
    return (x.sum()-x.max()-x.min())/(len(x)-2)
asd0 = df['angular_velocity'].rolling(100).apply(mean_nominmax).shift(-99)

asd = df['angular_velocity'].rolling(50).apply(mean_nominmax).shift(-49)
asd1 = df['angular_velocity'].rolling(3).apply(mean_nominmax).shift(-2)


px.line(y=[asd1, asd, asd0])

# Select data for the model

In [15]:
def prepare_to_tensorflow(frames, df):

    # data selection
    df = df.query('speed!=0')

    # match the data with the frame
    frame2data = df.groupby('exact_total_frame_idx')[['linacc0', 'linacc1', 'linacc2']].mean()
    outputs = df.groupby('offset_total_frame_idx')[['new_proportion']].mean()

    # the reindexed data
    frame_indices = outputs.index.values

    frames_reindexed = frames[frame_indices]
    other_inputs = frame2data.reindex(frame_indices)

    # screen out the nans
    nafilter = (~other_inputs.isna().any(axis=1)).values

    frames_reindexed = frames_reindexed[nafilter]
    other_inputs = other_inputs.values[nafilter]
    outputs = outputs.values[nafilter]
    
    
    return frames_reindexed, other_inputs/10, outputs

In [16]:
frames_in, other_in, out = prepare_to_tensorflow(frames, df)

In [17]:

from train_tools import validation_chunk_split

In [18]:
train_idx, val_idx = validation_chunk_split(len(frames_in), val_split=0.2)
train_frames, train_other, train_out = frames_in[train_idx], other_in[train_idx], out[train_idx]
val_frames, val_other, val_out = frames_in[val_idx], other_in[val_idx], out[val_idx]

# Model

In [20]:
def get_model(lr=.1, other_metrics=[]):
    tf.keras.backend.clear_session()
    image_shape = 64, 114, 3

    img_aug_preprocess_layers = [
        # keras.layers.RandomTranslation(0.05, 0.05, fill_mode='reflect'),
        # keras.layers.RandomRotation(0.02, fill_mode='reflect'),
        # keras.layers.RandomZoom(0.05, fill_mode='reflect'),
        # keras.layers.RandomContrast(0.5),
        # keras.layers.RandomBrightness([-0.7, 0.7])
    ]
    
    cnn_layers =  [
        keras.layers.Conv2D(16, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(32, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(64, 5, strides=2, activation='relu'),         
        keras.layers.Conv2D(64, 3, activation='relu'), 
        keras.layers.Conv2D(96, 3, activation='relu'),         
        keras.layers.Flatten(),
        keras.layers.Dropout(0.2),
    ]
    
    cnn = keras.Sequential(
        [
            keras.layers.InputLayer(image_shape),
            keras.layers.Rescaling(1/255), 
            *img_aug_preprocess_layers,
            *cnn_layers
        ])

    other_inputs = keras.layers.InputLayer((3,))
    x = keras.layers.Concatenate()([cnn.outputs[0], other_inputs.output])
    x = keras.layers.Dense(128, activation='relu')(x)
    x = keras.layers.Dense(64, activation='relu')(x)
    y = keras.layers.Dense(1, activation='sigmoid')(x)

    model = keras.Model([cnn.inputs[0], other_inputs.output], y)


    optimiser = keras.optimizers.Adam(lr)
    model.compile(optimizer=optimiser, loss='Huber', metrics=['MAE']+other_metrics)

    return model 

model = get_model()
model.summary()

Model: "functional_2"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 64, 114,   │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling           │ (None, 64, 114,   │          0 │ input_layer[0][0] │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d (Conv2D)     │ (None, 30, 55,    │      1,216 │ rescaling[0][0]   │
│                     │ 16)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_1 (Conv2D)   │ (None, 13, 26,    │     12,832 │ conv2d[0][0]      │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_2 (Conv2D)   │ (None, 5, 11, 64) │     51,264 │ conv2d_1[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_3 (Conv2D)   │ (None, 3, 9, 64)  │     36,928 │ conv2d_2[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_4 (Conv2D)   │ (None, 1, 7, 96)  │     55,392 │ conv2d_3[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ flatten (Flatten)   │ (None, 672)       │          0 │ conv2d_4[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout (Dropout)   │ (None, 672)       │          0 │ flatten[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_1       │ (None, 3)         │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate         │ (None, 675)       │          0 │ dropout[0][0],    │
│ (Concatenate)       │                   │            │ input_layer_1[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 128)       │     86,528 │ concatenate[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_1 (Dense)     │ (None, 64)        │      8,256 │ dense[0][0]       │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_2 (Dense)     │ (None, 1)         │         65 │ dense_1[0][0]     │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 252,481 (986.25 KB)

 Trainable params: 252,481 (986.25 KB)

 Non-trainable params: 0 (0.00 B)

In [21]:
from train_tools import find_lr, tg_notify, use_tensorboard, end_epoch_notify

In [22]:
find_lr(get_model(), [train_frames, train_other], train_out)
#tensorboard --logdir src/training/logs --bind_all

Epoch 1/100


I0000 00:00:1718100025.799393  757959 service.cc:145] XLA service 0x7b6950006370 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1718100025.799416  757959 service.cc:153]   StreamExecutor device (0): NVIDIA GeForce GTX 1650 SUPER, Compute Capability 7.5
2024-06-11 20:00:25.842681: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:268] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
2024-06-11 20:00:26.060961: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:465] Loaded cuDNN version 8907


 47/337 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - MAE: 0.1276 - loss: 0.0175

I0000 00:00:1718100029.196052  757959 device_compiler.h:188] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


337/337 ━━━━━━━━━━━━━━━━━━━━ 9s 13ms/step - MAE: 0.1257 - loss: 0.0166 - learning_rate: 1.0000e-06
Epoch 2/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - MAE: 0.1225 - loss: 0.0161 - learning_rate: 1.1220e-06
Epoch 3/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - MAE: 0.1215 - loss: 0.0160 - learning_rate: 1.2589e-06
Epoch 4/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - MAE: 0.1209 - loss: 0.0162 - learning_rate: 1.4125e-06
Epoch 5/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - MAE: 0.1207 - loss: 0.0160 - learning_rate: 1.5849e-06
Epoch 6/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - MAE: 0.1206 - loss: 0.0162 - learning_rate: 1.7783e-06
Epoch 7/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1201 - loss: 0.0159 - learning_rate: 1.9953e-06
Epoch 8/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - MAE: 0.1178 - loss: 0.0152 - learning_rate: 2.2387e-06
Epoch 9/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1202 - loss: 0.0158 - learning_rate: 2.5119e-06
Epoch 10/100
337/337 

In [23]:
model = get_model(3e-4)
model.fit(
    [train_frames, train_other],
    train_out,
    epochs=100, 
    validation_data = ([val_frames, val_other], val_out),
    callbacks=[
        tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10),
        use_tensorboard('training'), 
        end_epoch_notify()
        ] 
    )

Epoch 1/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 7s 13ms/step - MAE: 0.1216 - loss: 0.0165 - val_MAE: 0.1222 - val_loss: 0.0172
Epoch 2/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1208 - loss: 0.0160 - val_MAE: 0.1222 - val_loss: 0.0170
Epoch 3/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1189 - loss: 0.0158 - val_MAE: 0.1231 - val_loss: 0.0169
Epoch 4/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1196 - loss: 0.0155 - val_MAE: 0.1229 - val_loss: 0.0166
Epoch 5/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1222 - loss: 0.0159 - val_MAE: 0.1223 - val_loss: 0.0168
Epoch 6/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1168 - loss: 0.0143 - val_MAE: 0.1252 - val_loss: 0.0158
Epoch 7/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1157 - loss: 0.0138 - val_MAE: 0.1267 - val_loss: 0.0159
Epoch 8/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1187 - loss: 0.0135 - val_MAE: 0.1233 - val_loss: 0.0152
Epoch 9/100
337/337 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms

In [ ]:
#frames_reindexed#, other_inputs_reindexed, outputs

# visualise the performance

In [24]:

#train_frames, train_other, train_out
val_idx = np.sort(val_idx)
train_idx = np.sort(train_idx)

val_y_pred = model.predict([frames_in[val_idx], other_in[val_idx]], batch_size=64)
train_y_pred = model.predict([frames_in[train_idx], other_in[train_idx]], batch_size=64)


val_out = out[val_idx]
train_out = out[train_idx]



46/46 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step
169/169 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step


In [25]:
px.line(np.c_[train_out[:, 0], train_y_pred[:, 0]], title='train')

In [26]:
px.line(np.c_[val_out[:, 0], val_y_pred[:, 0]], title='val')